# README (Ignore if you are running on Mac/Linux)

If you are running on Windows, make sure you have started the Jupyter Notebook in a Bash shell.
Moreover, all the requirements below must be installed in this Bash (compatible) shell.

This can be achieved as follows:

1. Enable and install WSL(2) for Windows 10/11 [official documentation](https://docs.microsoft.com/en-us/windows/wsl/install)
    * On newer builds of W10/11 you can install WSL by running the following command in an *administrator* PowerShell terminal. Which will install by default an Ubuntu instance of WSL.
    ```bash
   wsl --install
    ```
2. Start the Ubuntu Bash shell by searching for `Bash` under Start, or by running `bash` in a (normal) PowerShell terminal.

Using a Bash terminal as started under step 2 above, you can install the Requirements as described below as if you are running it under Linux or Ubuntu/Debian.

## Requirements
These requirements may also be installed on Windows, however, development has only been tested on Linux/macOS.

Before we get started, first make sure to install all the required tools. We provide two lists below, one needed for setting up the testbed. And one for developing code to use with the testbed. Feel free to skip the installation of the second list, and return at a later point in time.


### Deployment

 > ⚠️ All dependencies must be installed in a Bash-compatible shell. For Windows users also see [above](#read-me)
Make sure to install a recent version of each of the dependencies.


 * (Windows only) Install every dependency in a Windows Subsystem for the Linux, Bash shell (see also README above).
 * GCloud SDK
    - Follow the installation instructions [here](https://cloud.google.com/sdk/docs/install), follow either the Linux installation instruction, or your OS/Distribution specific instructions.
    - Initialize the SDK with `gcloud init`, if prompted you may ignore to set/create a default/first project.
    - ⚠️ Run the command `gcloud auth application-default login`
        - ℹ️ We need to run this command to utilize your login credentials programmatically with terraform. This is needed as we will use these to impersonate a service account during the creation and setup of the Kubernetes cluster.
    - ⚠️ Run the command `gcloud components install beta`
        - ℹ️ We need to run this command to list the billing account IDs and enable billing. Currently, these features fall under beta access.
    - ⚠️ Run the command `gcloud components install gke-gcloud-auth-plugin`
        - ℹ️ We need to run this command to retrieve cluster configurations (to be used by `kubectl` and `helm`)
    - ⚠️ Run the command `gcloud auth configure-docker`
        - ℹ️ We need to run this command to push container images with docker to your project's container registry
 * Kubectl (>= 1.22.0)
 * Helm (>= 3.9.4)
 * Terraform (>= 1.2.8)
 * Python3.9/10
   * jupyter, ipython, bash_kernel
```bash
pip3 install -r requirements-jupyter.txt
python3 -m bash_kernel.install
```

### Development
For development, the following tools are needed/recommended:

 * Docker (>= 18.09).
    - If you don't have experience with using Docker, we recommend following [this](https://docs.docker.com/get-started/) tutorial.
 * Python3.9
 * pip3
 * JetBrains PyCharm

# Preparation

To make sure we can request resources on Google Cloud Platform (GCP), perform the following;

1. Create a GCP account on [https://cloud.google.com](https://cloud.google.com), using a Google account
2. Redeem your academic coupon on GCP, see Brightspace for information on obtaining the \\$50 academic coupon, or use the free \\$300 credits for new users provided by Google.


3. Make sure to use the `Bash` kernel, not a Python or other kernel. For those on windows machines, make sure to launch the `jupyter notebook` server from a bash-compliant command line, we recommend Windows Subsystem for Linux.

⚠️ Make sure to run this Notebook within a cloned repository, not standalone/downloaded from GitHub.


# Deployment

⚠️ This notebook assumes that commands are executed in order. Executing the provided commands multiple times should not result in issues. However, re-running cells with `cd` commands, or altering cells (other than variables as instructed) may result in unexpected behaviour.

## Getting started

First, we will set a few variables used **throughout** the project. We set them in this notebook for convenience, but they are also set to some example default values in configuration files for the project. If you change any of these, make sure to change the corresponding variables as well in;

* [`../terraform/terraform-gke/variables.tf`](../terraform/terraform-gke/variables.tf)
* [`../terraform/terraform-dependencies/variables.tf`](../terraform/terraform-dependencies/variables.tf)


> ⚠️ As you have changed the `PROJECT_ID` parameter to a unique project name, also change the `project_id` variable in the following files. This allows you to run `terraform apply` without having to override the default value for the project.

> ℹ️ Any variable changed here can also be provided to `terraform` using the `-var` flag, i.e.  `-var terraform_variable=$BASH_VARIABLE`. An example for setting the `project_id` variable is also provided later.

In [1]:
# VARIABLES THAT NEEDS TO BE SET

##################
### CHANGE ME! ###
##################
PROJECT_ID="test-bed-fltk-group16-mb"

# DEFAULT VARIABLES
ACCOUNT_ID="terraform-iam-service-account"
PRIVILEGED_ACCOUNT_ID="${ACCOUNT_ID}@${PROJECT_ID}.iam.gserviceaccount.com"
CLUSTER_NAME="fltk-testbed-cluster"
DEFAULT_POOL="default-node-pool"
EXPERIMENT_POOL="medium-fltk-pool-1"
REGION="us-central1-c"

TERRAFORM_GKE_DIR="../terraform/terraform-gke"
TERRAFORM_DEPENDENCIES_DIR="../terraform/terraform-dependencies"

## Project creation

Next, we create a project using the `PROJECT_ID` variable and get all the billing account information.

⁉️ (Ignore if using a pre-existing GCP Project) If the command below does not complete successfully, make sure to change the `PROJECT_ID` variable in the previous cell and re-run it.

In [2]:
gcloud projects create $PROJECT_ID --set-as-default
gcloud beta billing accounts list # Copy the Account ID of the account

Create in progress for [https://cloudresourcemanager.googleapis.com/v1/projects/test-bed-fltk-group16-mb].
Waiting for [operations/cp.5357798540755839027] to finish...done.              
Enabling service [cloudapis.googleapis.com] on project [test-bed-fltk-group16-mb]...
Operation "operations/acat.p2-821713242279-33d4d6c4-51b1-48cf-8366-7521b3d62142" finished successfully.
Updated property [core/project] to [test-bed-fltk-group16-mb].


Updates are available for some Google Cloud CLI components.  To install them,
please run:
  $ gcloud components update

ACCOUNT_ID            NAME                           OPEN  MASTER_ACCOUNT_ID
01B5D4-E14827-EE7D6E  Billing Account for Education  True


Copy the billing account identifier, e.g. `015594-41687F-092941`, and assign to the variable in the cell below

In [3]:
##################
### CHANGE ME! ###
##################
BILLING_ACCOUNT="01B5D4-E14827-EE7D6E"

Setup billing and enable services, this will allow us to create a GKE cluster (Google managed Kubernetes cluster), and push and pull containers to our private container repo.

In [4]:
# Setup billing to project
gcloud beta billing projects link $PROJECT_ID --billing-account $BILLING_ACCOUNT
# Enable services now billing is enabled
gcloud services enable compute container --project $PROJECT_ID

billingAccountName: billingAccounts/01B5D4-E14827-EE7D6E
billingEnabled: true
name: projects/test-bed-fltk-group16-mb/billingInfo
projectId: test-bed-fltk-group16-mb
Operation "operations/acf.p2-821713242279-f23abcc7-88c1-4a87-93ef-a72a5d2b866e" finished successfully.


## Creating a service-account

Create service account that has the minimum set of permissions for creating and managing a cluster. This service account
will be used to create the cluster, and deploy the dependencies that we use.

During the deployment we will make use of impersonation, to let *your* account utilize the service-account. For more information about this practise, see also [this](https://cloud.google.com/blog/topics/developers-practitioners/using-google-cloud-service-account-impersonation-your-terraform-code) blog by Google.

In [5]:
# Helper function to quickly enable gcp roles, assumes $PRIVILEGED_ACCOUNT_ID and $PROJECT_ID to be set.
function enable_gcp_role () {
  ROLE=$1
  gcloud projects add-iam-policy-binding \
    $PROJECT_ID \
    --member="serviceAccount:$PRIVILEGED_ACCOUNT_ID" \
    --role="roles/$ROLE"
}

# Create service-account
gcloud iam service-accounts create $ACCOUNT_ID --display-name="Terraform service account" --project ${PROJECT_ID}

# Allow the service account to use the the set of roles below.
enable_gcp_role "compute.viewer"                # Allow the service account to see active resources
enable_gcp_role "storage.objectViewer"          # Allow the service account/managed resources to pull from gcr.io (your code)
enable_gcp_role "compute.networkAdmin"          # Needed for setting up private network
enable_gcp_role "compute.securityAdmin"         # Needed for GKE
enable_gcp_role "container.clusterViewer"       # Needed for GKE
enable_gcp_role "container.clusterAdmin"        # Needed for GKE
enable_gcp_role "container.developer"           # Needed for GKE
enable_gcp_role "iam.serviceAccountAdmin"       # Needed for GKE
enable_gcp_role "iam.serviceAccountUser"        # Needed for GKE


Created service account [terraform-iam-service-account].
Updated IAM policy for project [test-bed-fltk-group16-mb].
bindings:
- members:
  - serviceAccount:service-821713242279@compute-system.iam.gserviceaccount.com
  role: roles/compute.serviceAgent
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/compute.viewer
- members:
  - serviceAccount:service-821713242279@container-engine-robot.iam.gserviceaccount.com
  role: roles/container.serviceAgent
- members:
  - serviceAccount:service-821713242279@containerregistry.iam.gserviceaccount.com
  role: roles/containerregistry.ServiceAgent
- members:
  - serviceAccount:821713242279-compute@developer.gserviceaccount.com
  - serviceAccount:821713242279@cloudservices.gserviceaccount.com
  role: roles/editor
- members:
  - user:bonfantimattia@gmail.com
  role: roles/owner
- members:
  - serviceAccount:service-821713242279@gcp-sa-pubsub.iam.gserviceaccount.com
  role: roles/pu

bindings:
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/compute.networkAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/compute.securityAdmin
- members:
  - serviceAccount:service-821713242279@compute-system.iam.gserviceaccount.com
  role: roles/compute.serviceAgent
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/compute.viewer
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/container.clusterAdmin
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/container.clusterViewer
- members:
  - serviceAccount:terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com
  role: roles/container.developer
- 

## Enable impersonation
With the service account created, we must enable impersonation, to allow the main account of the project to make use of the service account. For more information see also the [`add-iam-policy-binding`](https://cloud.google.com/sdk/gcloud/reference/iam/service-accounts/add-iam-policy-binding) reference.

Assign your `google_account` mail to the `OWNER_MAIL` variable, and run the command box below.

In [6]:
##################
### CHANGE ME! ###
##################
OWNER_MAIL="bonfantimattia@gmail.com"

gcloud iam service-accounts add-iam-policy-binding $PRIVILEGED_ACCOUNT_ID \
 --member="user:$OWNER_MAIL" \
 --role=roles/iam.serviceAccountTokenCreator \
 --project $PROJECT_ID

Updated IAM policy for serviceAccount [terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com].
bindings:
- members:
  - user:bonfantimattia@gmail.com
  role: roles/iam.serviceAccountTokenCreator
etag: BwXqhMwUfI0=
version: 1


To enable using your account's credentials, run the command below. This will open in a new tab/open the link that is displayed. Afterwards you can use your own credentials to impersonate the service account. 

You can, for example, also allow other google users (such as project members) to work with your cluster in this way.

In [7]:
gcloud auth application-default login

Your browser has been opened to visit:

    https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=764086051850-6qr4p6gpi6hn506pt8ejuq83di341hur.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A8085%2F&scope=openid+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fuserinfo.email+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fcloud-platform+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fsqlservice.login+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Faccounts.reauth&state=PffJnKUZ4hS18psSerhpKNAfcUrLIl&access_type=offline&code_challenge=N698KCl44kee6QDPkQ8rm_ab1etnq5yUey1hGYSata0&code_challenge_method=S256


Credentials saved to file: [/home/mattiacs/.config/gcloud/application_default_credentials.json]

These credentials will be used by any library that requests Application Default Credentials (ADC).

Quota project "test-bed-fltk-group16-mb" was added to ADC which can be used by Google client libraries for billing and quota. Note that some services may still bill the project own

## Creating a Google managed cluster (GKE)
To create the cluster, first change the active directory to the `terraform-gke` directory.

⚠️ Creating a cluster will incur billing cost on your project, by default the cluster will be small to minimize costs during this tutorial. Forgetting to `destroy` or scale down the cluster may result in quickly spending your academic coupon.

Init the directory, to initialize the Terraform module.

In [8]:
terraform -chdir=$TERRAFORM_GKE_DIR init 

Initializing modules...
- gcp-network in .terraform/modules/gcp-network
- gcp-network.firewall_rules in .terraform/modules/gcp-network/modules/firewall-rules
- gcp-network.routes in .terraform/modules/gcp-network/modules/routes
- gcp-network.subnets in .terraform/modules/gcp-network/modules/subnets
- gcp-network.vpc in .terraform/modules/gcp-network/modules/vpc
- gke in .terraform/modules/gke

Initializing the backend...

Initializing provider plugins...
- Finding hashicorp/google versions matching ">= 2.12.0, >= 3.45.0, >= 4.29.0, < 5.0.0"...
- Finding hashicorp/google-beta versions matching ">= 3.45.0, < 5.0.0"...
- Finding latest version of hashicorp/random...
- Finding hashicorp/kubernetes versions matching "~> 2.10"...
- Installing hashicorp/google v4.39.0...
- Installed hashicorp/google v4.39.0 (signed by HashiCorp)
- Installing hashicorp/google-beta v4.39.0...
- Installed hashicorp/google-beta v4.39.0 (signed by HashiCorp)
- Installing hashicorp/random v3.4.3...
- Installed hash

Next, we can check whether we can create a cluster. No warnings or errors should occur during this process. It may take a while to complete.

> ⚠️ We provide the project_id variable from `terraform/terraform-gke` manually, and also change the default value.

⁉️ If the command below does not complete successfully, e.g. after raising a `403` error, make sure that you have successfully created the project with `gcloud` earlier.


In [9]:
terraform -chdir=$TERRAFORM_GKE_DIR plan -var project_id=$PROJECT_ID

data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com]
module.gke.data.google_container_engine_versions.region: Reading...
data.google_client_config.default: Reading...
module.gke.data.google_compute_zones.available: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk-group16-mb/regions//zones/]
module.gke.data.google_compute_zones.available: Read complete after 1s [id=projects/test-bed-fltk-group16-mb/regions/us-central1]
module.gke.data.google_container_engine_versions.zone: Reading...
module.gke.data.google_container_engine_versions.region: Read complete after 1s [id=2022-10-08 12:12:26.916850652 +0000 UTC]
module.gke.data.google_container_engine_versions.zone: Read complete after 1s [id=2022-10-08 12:12:27.587629152 +0000 UTC]

Terraform used the selec

          + client_key             = (sensitive value)
          + cluster_ca_certificate = (known after apply)

          + client_certificate_config {
              + issue_client_certificate = false
            }
        }

      + mesh_certificates {
          + enable_certificates = (known after apply)
        }

      + monitoring_config {
          + enable_components = (known after apply)
        }

      + network_policy {
          + enabled = false
        }

      + node_config {
          + boot_disk_kms_key = (known after apply)
          + disk_size_gb      = (known after apply)
          + disk_type         = (known after apply)
          + guest_accelerator = (known after apply)
          + image_type        = (known after apply)
          + labels            = (known after apply)
          + local_ssd_count   = (known after apply)
          + machine_type      = (known after apply)
          + metadata          = (known after apply)
          + min_cpu_platform  = (kn

      + node_locations              = [
          + "us-central1-c",
        ]
      + operation                   = (known after apply)
      + project                     = "test-bed-fltk-group16-mb"
      + version                     = (known after apply)

      + autoscaling {
          + max_node_count = 100
          + min_node_count = 0
        }

      + management {
          + auto_repair  = true
          + auto_upgrade = true
        }

      + node_config {
          + disk_size_gb      = 64
          + disk_type         = "pd-standard"
          + guest_accelerator = []
          + image_type        = "COS_CONTAINERD"
          + labels            = {
              + "cluster_name"      = "fltk-testbed-cluster"
              + "default-node-pool" = "true"
              + "node_pool"         = "default-node-pool"
            }
          + local_ssd_count   = 0
          + machine_type      = "e2-medium"
          + metadata          = {
              + "cluster_name"     

      + input        = [
          + "us-central1-a",
          + "us-central1-b",
          + "us-central1-c",
          + "us-central1-f",
        ]
      + result       = (known after apply)
      + result_count = 3
    }

  # module.gke.random_string.cluster_service_account_suffix will be created
  + resource "random_string" "cluster_service_account_suffix" {
      + id          = (known after apply)
      + length      = 4
      + lower       = true
      + min_lower   = 0
      + min_numeric = 0
      + min_special = 0
      + min_upper   = 0
      + number      = true
      + numeric     = true
      + result      = (known after apply)
      + special     = false
      + upper       = false
    }

  # module.gcp-network.module.subnets.google_compute_subnetwork.subnetwork["us-central1/gcp-private-subnetwork"] will be created
  + resource "google_compute_subnetwork" "subnetwork" {
      + creation_timestamp         = (known after apply)
      + external_ipv6_prefix       = (known 

When the previous command completes successfully, we can start the deployment. Depending on any changes you may have done, this might take a while.

By default, this will create a private zonal cluster consisting of two node pools.

> ⚠️ A regional cluster (multi-zonal) will incur an additional fee of \\$ 0.10 /hour per managed (GKE) cluster. The **first** zonal cluster is free of this charge.

> ⚠️ By default spot/preemptive nodes are disabled. You can experiment by setting `spot` to true in the `tf` files. Note, however, that the default implementations provided in the testbed do not allow for recovery from getting spun down and rescheduled. Moreover, this may result in poor availability during busy hours in the region in which you deploy your cluster.


In [10]:
terraform -chdir=$TERRAFORM_GKE_DIR apply -auto-approve -var project_id=$PROJECT_ID

data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 1s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com]
module.gke.data.google_compute_zones.available: Reading...
data.google_client_config.default: Reading...
module.gke.data.google_container_engine_versions.region: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk-group16-mb/regions//zones/]
module.gke.data.google_compute_zones.available: Read complete after 1s [id=projects/test-bed-fltk-group16-mb/regions/us-central1]
module.gke.data.google_container_engine_versions.region: Read complete after 1s [id=2022-10-08 12:13:23.089823647 +0000 UTC]
module.gke.data.google_container_engine_versions.zone: Reading...
module.gke.data.google_container_engine_versions.zone: Read complete after 1s [id=2022-10-08 12:13:23.806256982 +0000 UTC]

Terraform used the selec

          + client_key             = (sensitive value)
          + cluster_ca_certificate = (known after apply)

          + client_certificate_config {
              + issue_client_certificate = false
            }
        }

      + mesh_certificates {
          + enable_certificates = (known after apply)
        }

      + monitoring_config {
          + enable_components = (known after apply)
        }

      + network_policy {
          + enabled = false
        }

      + node_config {
          + boot_disk_kms_key = (known after apply)
          + disk_size_gb      = (known after apply)
          + disk_type         = (known after apply)
          + guest_accelerator = (known after apply)
          + image_type        = (known after apply)
          + labels            = (known after apply)
          + local_ssd_count   = (known after apply)
          + machine_type      = (known after apply)
          + metadata          = (known after apply)
          + min_cpu_platform  = (kn

      + node_locations              = [
          + "us-central1-c",
        ]
      + operation                   = (known after apply)
      + project                     = "test-bed-fltk-group16-mb"
      + version                     = (known after apply)

      + autoscaling {
          + max_node_count = 100
          + min_node_count = 0
        }

      + management {
          + auto_repair  = true
          + auto_upgrade = true
        }

      + node_config {
          + disk_size_gb      = 64
          + disk_type         = "pd-standard"
          + guest_accelerator = []
          + image_type        = "COS_CONTAINERD"
          + labels            = {
              + "cluster_name"      = "fltk-testbed-cluster"
              + "default-node-pool" = "true"
              + "node_pool"         = "default-node-pool"
            }
          + local_ssd_count   = 0
          + machine_type      = "e2-medium"
          + metadata          = {
              + "cluster_name"     

      + input        = [
          + "us-central1-a",
          + "us-central1-b",
          + "us-central1-c",
          + "us-central1-f",
        ]
      + result       = (known after apply)
      + result_count = 3
    }

  # module.gke.random_string.cluster_service_account_suffix will be created
  + resource "random_string" "cluster_service_account_suffix" {
      + id          = (known after apply)
      + length      = 4
      + lower       = true
      + min_lower   = 0
      + min_numeric = 0
      + min_special = 0
      + min_upper   = 0
      + number      = true
      + numeric     = true
      + result      = (known after apply)
      + special     = false
      + upper       = false
    }

  # module.gcp-network.module.subnets.google_compute_subnetwork.subnetwork["us-central1/gcp-private-subnetwork"] will be created
  + resource "google_compute_subnetwork" "subnetwork" {
      + creation_timestamp         = (known after apply)
      + external_ipv6_prefix       = (known 

module.gke.google_container_cluster.primary: Still creating... 10s elapsed]
module.gke.google_container_cluster.primary: Still creating... 20s elapsed]
module.gke.google_container_cluster.primary: Creation complete after 2m30s [id=projects/test-bed-fltk-group16-mb/locations/us-central1-c/clusters/fltk-testbed-cluster]
module.gke.google_container_node_pool.pools["default-node-pool"]: Creating...
module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Creating...
module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Still creating... [10s elapsed]
module.gke.google_container_node_pool.pools["default-node-pool"]: Still creating... [10s elapsed]
module.gke.google_container_node_pool.pools["medium-fltk-pool-1"]: Still creating... [20s elapsed]
module.gke.google_container_node_pool.pools["default-node-pool"]: Still creating... [20s elapsed]
module.gke.google_container_node_pool.pools["default-node-pool"]: Still creating... [30s elapsed]
module.gke.google_container_nod

Next, we add cluster credentials (so you can interact with the cluster through `kubectl` an `helm`).

In [11]:
# Add credentials for interacting with cluster via kubectl
gcloud container clusters get-credentials $CLUSTER_NAME --region $REGION --project $PROJECT_ID

Fetching cluster endpoint and auth data.
kubeconfig entry generated for fltk-testbed-cluster.


⚠️ The cluster by default does not contain any nodes in the node pools, the `initial_node_count` is set to 0.

Lastly, we need to scale up the cluster, as by default we create a cluster with nodepools of size 0.

In [12]:
###
### ! CHANGE ME
###
MAX_NUM_NODES=4

gcloud container clusters update $CLUSTER_NAME --node-pool $DEFAULT_POOL \
    --no-enable-autoscaling --region $REGION --quiet
    
# The high performance node will scale up automatically whenever the workloads are deployed
gcloud container clusters update $CLUSTER_NAME --node-pool $EXPERIMENT_POOL \
    --enable-autoscaling --min-nodes=0 --max-nodes=$MAX_NUM_NODES --region $REGION --quiet

gcloud container clusters resize $CLUSTER_NAME --node-pool $DEFAULT_POOL \
    --num-nodes 1 --region $REGION --quiet


Default change: During creation of nodepools or autoscaling configuration changes for cluster versions greater than 1.24.1-gke.800 a default location policy is applied. For Spot and PVM it defaults to ANY, and for all other VM kinds a BALANCED policy is used. To change the default values use the `--location-policy` flag.
Updating fltk-testbed-cluster...done.                                          
Updated [https://container.googleapis.com/v1/projects/test-bed-fltk-group16-mb/zones/us-central1-c/clusters/fltk-testbed-cluster].
To inspect the contents of your cluster, go to: https://console.cloud.google.com/kubernetes/workload_/gcloud/us-central1-c/fltk-testbed-cluster?project=test-bed-fltk-group16-mb
Default change: During creation of nodepools or autoscaling configuration changes for cluster versions greater than 1.24.1-gke.800 a default location policy is applied. For Spot and PVM it defaults to ANY, and for all other VM kinds a BALANCED policy is used. To change the default values 

### Changing deployment

To save cost, or run different experiments, you might want to change the configuration of your cluster. This can be achieved by modifying the cluster configuration in the [`terraform-gke/main.tf`](../terraform/terraform-gke/main.tf) configuration file. You can change the default node-pools, create additional node pools with taints (to allow for scheduling on specific nodes/pools) and much more.

After finishing your changes, simply run the following commands

```bash
# Use `plan` to check your configuration
terraform plan
# Check to see if your changes are as expected, terraform will show what will be created/removed.

# If the changes are as you expect, apply the changes.
terraform apply #-auto-approve
```

Depending on the number of changes, this may take some time.

## Installing dependencies
Lastly, we need to install the dependencies on our cluster. First change the directories, and then run the `init`, `plan` and `apply` commands as we did for creating the GKE cluster.

Init the directory, to initialize the Terraform module.

In [13]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR init -reconfigure


Initializing the backend...

Initializing provider plugins...
- Finding latest version of hashicorp/helm...
- Finding kbst/kustomization versions matching ">= 0.7.0"...
- Finding gavinbunney/kubectl versions matching ">= 1.13.1"...
- Finding hashicorp/kubernetes versions matching ">= 1.13.1"...
- Finding latest version of hashicorp/google...
- Installing hashicorp/google v4.39.0...
- Installed hashicorp/google v4.39.0 (signed by HashiCorp)
- Installing hashicorp/helm v2.7.0...
- Installed hashicorp/helm v2.7.0 (signed by HashiCorp)
- Installing kbst/kustomization v0.9.0...
- Installed kbst/kustomization v0.9.0 (self-signed, key ID A72E13094BE75DDF)
- Installing gavinbunney/kubectl v1.14.0...
- Installed gavinbunney/kubectl v1.14.0 (self-signed, key ID AD64217B5ADD572F)
- Installing hashicorp/kubernetes v2.14.0...
- Installed hashicorp/kubernetes v2.14.0 (signed by HashiCorp)

Partner and community providers are signed by their developers.
If you'd like to know more about provider sign

Check to see if we can plan the deployment. This will setup the following:

* Kubeflow training operator (used to deploy and manage PyTorchTrainJobs programmatically)
* NFS-provisioner (used to enable logging on a persistent `ReadWriteMany` PVC in the cluster)


In [14]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR plan -var project_id=$PROJECT_ID

data.kustomization_build.training_operator: Reading...
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com]
data.google_client_config.default: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk-group16-mb/regions//zones/]
data.google_container_cluster.testbed_cluster: Reading...
data.kustomization_build.training_operator: Read complete after 2s [id=a294ea9a3d4f626ec1ec55aac66b4a486f682fe5dbec2eadf58d30baee14a8f66a3ec2674c0e2d9a40e7bc191f878f010393849f4581c6a4189bc41761abab89]
data.google_container_cluster.testbed_cluster: Read complete after 2s [id=projects/test-bed-fltk-group16-mb/locations/us-central1-c/clusters/fltk-testbed-cluster]

Terraform used the selected providers to generate the following execution plan.
Resource actions are indicated with th

      + manifest = jsonencode(
            {
              + apiVersion = "v1"
              + kind       = "Service"
              + metadata   = {
                  + annotations = {
                      + "prometheus.io/path"   = "/metrics"
                      + "prometheus.io/port"   = "8080"
                      + "prometheus.io/scrape" = "true"
                    }
                  + labels      = {
                      + app = "training-operator"
                    }
                  + name        = "training-operator"
                  + namespace   = "kubeflow"
                }
              + spec       = {
                  + ports    = [
                      + {
                          + name       = "monitoring-port"
                          + port       = 8080
                          + targetPort = 8080
                        },
                    ]
                  + selector = {
                      + control-plane = "kubeflow-training-operator"
    

                                                          + template      = {
                                                              + description = "Template is the object that describes the pod that will be created for this replica. RestartPolicy in PodTemplateSpec will be overide by RestartPolicy in ReplicaSpec"
                                                              + properties  = {
                                                                  + metadata = {
                                                                      + description = "Standard object's metadata. More info: https://git.k8s.io/community/contributors/devel/sig-architecture/api-conventions.md#metadata"
                                                                      + properties  = {
                                                                          + annotations = {
                                                                              + additionalProperties = {
          

                                                                                                                      + properties  = {
                                                                                                                          + key      = {
                                                                                                                              + description = "The label key that the selector applies to."
                                                                                                                              + type        = "string"
                                                                                                                            }
                                                                                                                          + operator = {
                                                                                                                             

                                                                                                                        ]
                                                                                                                      + type        = "object"
                                                                                                                    }
                                                                                                                  + type        = "array"
                                                                                                                }
                                                                                                            }
                                                                                                          + type        = "object"
                                                                                                        }
                  

...

                                                                                                  + description = "The seccomp options to use by this container. If seccomp options are provided at both the pod & container level, the container options override the pod options."
                                                                                                  + properties  = {
                                                                                                      + localhostProfile = {
                                                                                                          + description = "localhostProfile indicates a profile defined in a file on the node should be used. The profile must be preconfigured on the node to work. Must be a descending path, relative to the kubelet's configured seccomp profile location. Must only be set if type is \"Localhost\"."
                                                                                       

                                                                                                          + items       = {
                                                                                                              + type = "string"
                                                                                                            }
                                                                                                          + type        = "array"
                                                                                                        }
                                                                                                    }
                                                                                                  + type        = "object"
                                                                                                }
                                                                               

                                                          + labelSelector = {
                                                              + description = "A label selector is a label query over a set of resources. The result of matchLabels and matchExpressions are ANDed. An empty label selector matches all objects. A null label selector matches no objects."
                                                              + properties  = {
                                                                  + matchExpressions = {
                                                                      + description = "matchExpressions is a list of label selector requirements. The requirements are ANDed."
                                                                      + items       = {
                                                                          + description = "A label selector requirement is a selector that contains values, a key, and an operator that relates the key and va

  + resource "kustomization_resource" "training_operator" {
      + id       = (known after apply)
      + manifest = jsonencode(
            {
              + apiVersion = "apps/v1"
              + kind       = "Deployment"
              + metadata   = {
                  + labels    = {
                      + control-plane = "kubeflow-training-operator"
                    }
                  + name      = "training-operator"
                  + namespace = "kubeflow"
                }
              + spec       = {
                  + replicas = 1
                  + selector = {
                      + matchLabels = {
                          + control-plane = "kubeflow-training-operator"
                        }
                    }
                  + template = {
                      + metadata = {
                          + annotations = {
                              + "sidecar.istio.io/inject" = "false"
                            }
                          + labels  

                          + "*",
                        ]
                    },
                  + {
                      + apiGroups = [
                          + "apps",
                          + "extensions",
                        ]
                      + resources = [
                          + "deployments",
                        ]
                      + verbs     = [
                          + "*",
                        ]
                    },
                  + {
                      + apiGroups = [
                          + "",
                        ]
                      + resources = [
                          + "pods/exec",
                        ]
                      + verbs     = [
                          + "create",
                        ]
                    },
                  + {
                      + apiGroups = [
                          + "rbac.authorization.k8s.io",
                        ]
                      + resources = 

When the previous command completes successfully, we can start the deployment. This will install the NFS provisioner and Kubeflow Training Operator dependencies


In [15]:
terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR apply -auto-approve -var project_id=$PROJECT_ID

data.kustomization_build.training_operator: Reading...
data.google_service_account_access_token.default: Reading...
data.google_service_account_access_token.default: Read complete after 0s [id=projects/-/serviceAccounts/terraform-iam-service-account@test-bed-fltk-group16-mb.iam.gserviceaccount.com]
data.google_client_config.default: Reading...
data.google_client_config.default: Read complete after 0s [id=projects/test-bed-fltk-group16-mb/regions//zones/]
data.google_container_cluster.testbed_cluster: Reading...
data.kustomization_build.training_operator: Still reading... [10s elapsed]
data.google_container_cluster.testbed_cluster: Still reading... [10s elapsed]
data.google_container_cluster.testbed_cluster: Read complete after 10s [id=projects/test-bed-fltk-group16-mb/locations/us-central1-c/clusters/fltk-testbed-cluster]
data.kustomization_build.training_operator: Read complete after 13s [id=a294ea9a3d4f626ec1ec55aac66b4a486f682fe5dbec2eadf58d30baee14a8f66a3ec2674c0e2d9a40e7bc191f878f

  + resource "kustomization_resource" "training_operator" {
      + id       = (known after apply)
      + manifest = jsonencode(
            {
              + apiVersion = "v1"
              + kind       = "Service"
              + metadata   = {
                  + annotations = {
                      + "prometheus.io/path"   = "/metrics"
                      + "prometheus.io/port"   = "8080"
                      + "prometheus.io/scrape" = "true"
                    }
                  + labels      = {
                      + app = "training-operator"
                    }
                  + name        = "training-operator"
                  + namespace   = "kubeflow"
                }
              + spec       = {
                  + ports    = [
                      + {
                          + name       = "monitoring-port"
                          + port       = 8080
                          + targetPort = 8080
                        },
                    ]
       

                                                            }
                                                          + template      = {
                                                              + description = "Template is the object that describes the pod that will be created for this replica. RestartPolicy in PodTemplateSpec will be overide by RestartPolicy in ReplicaSpec"
                                                              + properties  = {
                                                                  + metadata = {
                                                                      + description = "Standard object's metadata. More info: https://git.k8s.io/community/contributors/devel/sig-architecture/api-conventions.md#metadata"
                                                                      + properties  = {
                                                                          + annotations = {
                                                     

                                                                                                                      + properties  = {
                                                                                                                          + key      = {
                                                                                                                              + description = "The label key that the selector applies to."
                                                                                                                              + type        = "string"
                                                                                                                            }
                                                                                                                          + operator = {
                                                                                                                             

                                                                                                                        ]
                                                                                                                      + type        = "object"
                                                                                                                    }
                                                                                                                  + type        = "array"
                                                                                                                }
                                                                                                            }
                                                                                                          + type        = "object"
                                                                                                        }
                  

...

                                                                                                  + type        = "string"
                                                                                                }
                                                                                              + system           = {
                                                                                                  + description = "The name of the storage system as configured in ScaleIO."
                                                                                                  + type        = "string"
                                                                                                }
                                                                                              + volumeName       = {
                                                                                                  + description = "The name of a volume already created

                                                                                                }
                                                                                              + optional    = {
                                                                                                  + description = "Specify whether the Secret or its keys must be defined"
                                                                                                  + type        = "boolean"
                                                                                                }
                                                                                              + secretName  = {
                                                                                                  + description = "Name of the secret in the pod's namespace to use. More info: https://kubernetes.io/docs/concepts/storage/volumes#secret"
                                                 

                                                                                                }
                                                                                              + storagePolicyName = {
                                                                                                  + description = "Storage Policy Based Management (SPBM) profile name."
                                                                                                  + type        = "string"
                                                                                                }
                                                                                              + volumePath        = {
                                                                                                  + description = "Path that identifies vSphere volume vmdk"
                                                                                                  + type        = "stri

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



helm_release.nfs_client_provisioner: Still creating... [20s elapsed]
helm_release.nfs_client_provisioner: Still creating... [30s elapsed]
helm_release.nfs_client_provisioner: Still creating... [40s elapsed]
helm_release.nfs_client_provisioner: Still creating... [50s elapsed]
helm_release.nfs_client_provisioner: Creation complete after 53s [id=nfs-server]

Apply complete! Resources: 12 added, 0 changed, 0 destroyed.


## Deploying extractor

Lastly, we deploy the extractor pod, which also provides PVCs which can be used for artifact retrieval.

Retrieval can be done by running

```bash
EXTRACTOR_POD_NAME=$(kubectl get pods -n test -l "app.kubernetes.io/name=fltk.extractor" -o jsonpath="{.items[0].metadata.name}")
kubectl cp -n test $EXTRACTOR_POD_NAME:/opt/federation-lab/logging ./logging
```

For copying from the extractor path `/opt/federation-lab/logging` to a directory locally named `logging`.

First build the docker container, following the instructions of the [readme](https://github.com/JMGaljaard/fltk-testbed#creating-and-uploading-docker-container).


N.B. Make sure to have setup a working authentication provider for docker, such that you can push to your repository.

Run this in a terminal in the content-root directory (so `fltk-testbed` if the project name was not altered).
```bash
python3 -m venv venv
source venv
pip3 install -r requirements-cpu.txt
python3 -m fltk extractor configs/example_cloud_experiment.json
```

Make sure to have run `gcloud auth configure-docker` in an external terminal.

Make sure to allow docker to build/push/run without `sudo` [link](https://cloud.google.com/artifact-registry/docs/docker/authentication).


In [16]:
# Build the docker container with buildkit. Make sure you have Docker Desktop running on Windows/MacOS
DOCKER_BUILDKIT=1 docker build --platform linux/amd64 ../ --tag gcr.io/$PROJECT_ID/fltk
docker push gcr.io/$PROJECT_ID/fltk

[+] Building 0.0s (0/1)                                                         
[+] Building 0.2s (2/3)                                                         
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          0.1s
[+] Building 0.3s (2/3)                                                         
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for dock

 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.0s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
[+] Building 2.3s (3/4)                                                         
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.2s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
[+] Building 2.4s (3/4)                

 => => transferring context: 146.40MB                                      0.6s
[+] Building 3.2s (5/14)                                                        
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.4s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf  0.7s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf41760be7  0.0s
 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea

 => => transferring context: 335.96MB                                      1.3s
[+] Building 3.9s (5/14)                                                        
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.4s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf  1.4s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf41760be7  0.0s
 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea

 => => transferring context: 516.59MB                                      2.0s
[+] Building 4.6s (6/14)                                                        
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 765B                                       0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.4s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf  2.1s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf41760be7  0.0s
 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea

...

 => => extracting sha256:52229f64bc4eb88d1ebf114ea150563e4f51eac04ffbff93  7.8s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [internal] load build context                                          2.1s
 => => transferring context: 525.34MB                                      2.0s
 => [stage-0 2/8] WORKDIR /opt/federation-lab                              1.2s
 => [stage-0 3/8] ADD data/ data/                                          0.6s
 => [stage-0 4/8] COPY requirements-cpu.txt ./requirements.txt             0.0s
 => [stage-0 5/8] RUN --mount=type=cache,target=/root/.cache/pip,mode=0  101.0s
 => [stage-0 6/8] ADD fltk fltk                                            0.0s
 => [stage-0 7/8] ADD configs configs                                      0.1s
 => [stage-0 8/8] ADD experiments experiments                              0.0s
 => exporting to image                                                     1.2s
 => => exporting layers                 

 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea150563e4f51ea 611.67MB / 611.67MB  18.6s
 => => extracting sha256:52229f64bc4eb88d1ebf114ea150563e4f51eac04ffbff93  7.8s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [internal] load build context                                          2.1s
 => => transferring context: 525.34MB                                      2.0s
 => [stage-0 2/8] WORKDIR /opt/federation-lab                              1.2s
 => [stage-0 3/8] ADD data/ data/                                          0.6s
 => [stage-0 4/8] COPY requirements-cpu.txt ./requirements.txt             0.0s
 => [stage-0 5/8] RUN --mount=type=cache,target=/root/.cache/pip,mode=0  101.0s
 => [stage-0 6/8] ADD fltk fltk                                            0.0s
 => [stage-0 7/8] ADD configs configs   

 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaa  26.6s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf41760be7  0.0s
 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea150563e4f51ea 611.67MB / 611.67MB  18.6s
 => => extracting sha256:52229f64bc4eb88d1ebf114ea150563e4f51eac04ffbff93  7.8s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [internal] load build context                                          2.1s
 => => transferring context: 525.34MB                                      2.0s
 => [stage-0 2/8] WORKDIR /opt/federation-lab                              1.2s
 => [stage-0 3/8] ADD data/ data/                                          0.6s
 => [stage-0 4/8] COPY requirements-cpu.

 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 141B                                          0.0s
 => [internal] load metadata for docker.io/bitnami/pytorch:1.12.1          2.4s
 => [auth] bitnami/pytorch:pull token for registry-1.docker.io             0.0s
 => [stage-0 1/8] FROM docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaa  26.6s
 => => resolve docker.io/bitnami/pytorch:1.12.1@sha256:7ce18dfaaf41760be7  0.0s
 => => sha256:7ce18dfaaf41760be7c1e9a0ab916226ba60f7c0774d7a6 742B / 742B  0.0s
 => => sha256:f8f6055f1b1f806457e9b899403b58f282346b4e8fc 7.06kB / 7.06kB  0.0s
 => => sha256:52229f64bc4eb88d1ebf114ea150563e4f51ea 611.67MB / 611.67MB  18.6s
 => => extracting sha256:52229f64bc4eb88d1ebf114ea150563e4f51eac04ffbff93  7.8s
 => CACHED [internal] settings cache mount permissions                     0.0s
 => [internal] load build context                                          2.1s
 => => transferring context: 525.34MB   

 => [stage-0 8/8] ADD experiments experiments                              0.0s
 => exporting to image                                                     3.2s
 => => exporting layers                                                    3.2s
 => => writing image sha256:89a5a884d2d822545c0d301c9364cd22a74219fe38bac  0.0s
 => => naming to gcr.io/test-bed-fltk-group16-mb/fltk                      0.0s
Using default tag: latest
The push refers to repository [gcr.io/test-bed-fltk-group16-mb/fltk]

996acf52: Preparing 
9ed9d97d: Preparing 
753e2576: Preparing 
ad97015c: Preparing 
e4dc4f29: Preparing 
c28d9aac: Preparing 
f957b4f5: Preparing 
92ee7b50: Preparing 
latest: digest: sha256:4ac30d45333e48ed31f756dc07c046743a9da54226adfa02814df06f99cc4088 size: 2207


In [17]:
# Install the extractor, and set the projectName to $PROJECT_ID.
# In case you get a warning regarding the namespace test, this means that the dependencies have not been properly installed.
# Make sure to check whether you have enough resources available, and re-run the installation of dependencies. (see above).

# Deploy extractor, in test namespace with updated image reference (--set overwrites values from `fltk-values.yaml`).
helm install extractor ../charts/extractor -f ../charts/fltk-values.yaml --namespace test --set provider.projectName=$PROJECT_ID

W1008 14:41:19.147930   14951 gcp.go:120] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.25+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
NAME: extractor
LAST DEPLOYED: Sat Oct  8 14:41:21 2022
NAMESPACE: test
STATUS: deployed
REVISION: 1
TEST SUITE: None
NOTES:
Get the FLTK extractors Tensorboard URL by running:

export POD_NAME=$(kubectl get pods -n test -l "app.kubernetes.io/name=fltk.extractor" -o jsonpath="{.items[0].metadata.name}")
echo http://localhost:6006/
kubectl -n test port-forward $POD_NAME 6006:6006


## Testing the deployment

To make sure that the deployment went OK, we can run the following command to test whether we can use Pytorch-Training operators.

This will create a simple deployment using a Kubeflow pytorch example job.

This will create a small (1 master, 1 client) training job on mnist on your cluster. You can follow the deployment by navigating to your cluster on [cloud.google.com](cloud.google.com)

In [18]:
# This cell is optional, but the next shell should show that a pytorch train job is created.
kubectl create -f https://raw.githubusercontent.com/kubeflow/training-operator/master/examples/pytorch/simple.yaml

W1008 14:45:42.331383   15280 gcp.go:119] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.26+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
pytorchjob.kubeflow.org/pytorch-simple created


In [19]:
# Retrieve all CRD Pytorchjob from Kubeflow.
kubectl get pytorchjobs.kubeflow.org --all-namespaces

# Alternatively, we can remove all jobs, this will remove all information and logs as well.
kubectl delete pytorchjobs.kubeflow.org --all-namespaces --all

W1008 14:53:12.170066   15818 gcp.go:119] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.26+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
NAMESPACE   NAME             STATE     AGE
kubeflow    pytorch-simple   Running   7m29s
W1008 14:53:14.073162   15834 gcp.go:119] WARNING: the gcp auth plugin is deprecated in v1.22+, unavailable in v1.26+; use gcloud instead.
To learn more, consult https://cloud.google.com/blog/products/containers-kubernetes/kubectl-auth-changes-in-gke
pytorchjob.kubeflow.org "pytorch-simple" deleted


# Cleaning up

## Scaling down the cluster

This is the preferred way to scale down.
Scale node pools down to prevent idle resource utilization.

In [20]:
gcloud container clusters resize $CLUSTER_NAME --node-pool $DEFAULT_POOL \
     --num-nodes 0 --region $REGION --quiet

gcloud container clusters resize $CLUSTER_NAME --node-pool $EXPERIMENT_POOL \
    --num-nodes 0 --region $REGION --quiet

Resizing fltk-testbed-cluster...done.


Updated [https://container.googleapis.com/v1/projects/test-bed-fltk-group16-mb/zones/us-central1-c/clusters/fltk-testbed-cluster].
Resizing fltk-testbed-cluster...done.                                          
Updated [https://container.googleapis.com/v1/projects/test-bed-fltk-group16-mb/zones/us-central1-c/clusters/fltk-testbed-cluster].


## Destroying the cluster

> ⚠️ THIS WILL REMOVE YOUR CLUSTER AND DATA STORED ON IT. For this tutorial's purpose destroying your cluster is not an issue. For testing/developing, we recommend manually scaling your cluster up and down instead.

To clean up/remove the cluster, we will use the `terraform destroy` command.

 * Running it in `terraform-dependencies` WILL REMOVE the Kubeflow Training-Operator from your cluster.
 * Running it in `terraform-gke` WILL REMOVE YOU ENTIRE CLUSTER.

You can uncomment the commands below to remove the cluster, or run the command in a terminal in the [`../terraform/terraform-gke`](../terraform/terraform-gke) directory.

> ⚠️ It is recommended to scale down the cluster/nodepools rather then destroying, refer to the last code block.

In [ ]:
# THIS WILL REMOVE/TEARDOWN YOUR CLUSTER, ONLY RECOMMENDED FOR TESTING THE DEPLOYMENT

# terraform -chdir=$TERRAFORM_DEPENDENCIES_DIR destroy -auto-approve -var project_id=$PROJECT_ID

# terraform -chdir=$TERRAFORM_GKE_DIR destroy -auto-approve -var project_id=$PROJECT_ID